# Fetching Reaktor data

In [2]:
import pandas as pd
data = pd.read_csv("nsights_cleaned.csv")

In [3]:
import numpy as np
relevant_zips = data.groupby("zip_code").count().sort_values(by="latitude", ascending=False).head(59).index.tolist()
perttu = data[data.zip_code.isin(relevant_zips)]
perttu = perttu[perttu.build_year >= 1950].reset_index(drop=True)
perttu['century'] = np.floor(perttu.build_year/10)*10

In [4]:
perttu_out = perttu.groupby(["zip_code", "city", "century", "new_development"]).agg(
    ["mean", "count"])['rent_per_sqm'].reset_index()
perttu_out.rename({"mean": "rent_per_sqm", "count": "rows"}, axis=1, inplace=True)

In [5]:
perttu_out.to_excel("Perttu zip overview.xlsx", index=False)

In [6]:
relevant_cities = data.groupby("city").count().sort_values(by="street", ascending=False).head(15).index.to_list()
perttu = data[data.city.isin(relevant_cities)]
perttu = perttu[perttu.build_year >= 1950].reset_index(drop=True)
perttu['century'] = np.floor(perttu.build_year/10)*10

In [7]:
perttu_out = perttu.groupby(["city", "century", "new_development"]).agg(["mean", "count"])['rent_per_sqm'].reset_index()
perttu_out.rename({"mean": "rent_per_sqm", "count": "rows"}, axis=1, inplace=True)
perttu_out.to_excel("Perttu City overview.xlsx", index=False)

Getting Reaktor data

In [8]:
import requests
response = requests.get("https://raw.githubusercontent.com/reaktor/Neliohinnat/master/update_2021/json/trends.json")
df = pd.DataFrame.from_dict(response.json()).transpose().reset_index()

In [9]:
df_final = df[['index', 'hinta2020', 'trendi2020']].rename({"index": "zip_code",
                                                 "hinta2020": "price_per_sqm", 
                                                 "trendi2020": "change"}, axis=1)

In [10]:
grouped_data = data.groupby(["zip_code", "city"]).mean()['rent_per_sqm'].reset_index()
grouped_data.zip_code = grouped_data.zip_code.astype(str)
for i in range(len(grouped_data)):
    if len(grouped_data.loc[i, "zip_code"]) == 3:
        grouped_data.loc[i, "zip_code"] = "00" + str(grouped_data.loc[i, "zip_code"])
    elif len(grouped_data.loc[i, "zip_code"]) == 4:
        grouped_data.loc[i, "zip_code"] = "0" + str(grouped_data.loc[i, "zip_code"])

In [11]:
merged = pd.merge(df_final, grouped_data, on="zip_code")
merged['ratio'] = (merged['rent_per_sqm']/merged['price_per_sqm'])*100

In [12]:
merged.rename({"zip_code": "pnro"}, axis=1, inplace=True)

# Plotting topojson

In [13]:
import json
with open('fi_zips.topojson', encoding="utf-8") as f:
      states_topo = json.load(f)

In [14]:
# adding features to topojson dictionary
for city in states_topo['objects']['pnro']['geometries']:
    dict_zip = city['properties']['pnro']
    if dict_zip in merged.pnro.to_list():
        relevant_row = merged[merged['pnro'] == dict_zip]
        city['properties']['price_per_sqm'] = relevant_row.price_per_sqm.values[0]
        city['properties']['rent_per_sqm'] = round(relevant_row.rent_per_sqm.values[0], 2)
        city['properties']['change'] = round(relevant_row.change.values[0],2)
        city['properties']['ratio2'] = round(relevant_row.ratio.values[0],2)

In [17]:
import folium
max_ratio = 1.5
merged.loc[lambda x: x.ratio > max_ratio, "ratio"] = max_ratio
folium_map = folium.Map(location=[60.16, 24.9], zoom_start=7, tiles = "cartodbpositron")
choropleth = folium.Choropleth(geo_data=states_topo,
                  topojson='objects.pnro',
                  key_on = "feature.properties.pnro",
                  data = merged,
                  columns = ["pnro", "ratio"],
                  fill_color= "RdYlGn",
                  line_opacity=0.2).add_to(folium_map)

choropleth.geojson.add_child(folium.features.GeoJsonTooltip(
    fields=["pnro", 'name', "mncplty", "price_per_sqm", "rent_per_sqm", "ratio2", "change"],
    aliases=["Zip Code", "City", "Municipality", "Price pr. sqm. (EUR)", "Rent pr. sqm. (EUR)", "Ratio (%)",
             "Change in sales to previous year (%)"]))

folium_map